In [2]:
import pandas as pd
from igraph import * 

In [3]:
network = pd.read_csv("fakeNewsDatasetTopic3Topics40pass.csv")
#list(network.columns.values)


The dataset used is about fake news which was collected from period of 09-02-2017 to 18-03-2017, the tweets hashtags included one or more of the following hashtags: alternativefacts, fakenews, truthiness, postfact,posttruth, and factcheck. The problem which we faced with the dataset is that it wasnt labeled with topic of fake news. Therefore we had to create topics for the dataset, this was done by means of topic modeling which is provided in the other file.

the topics of the dataset after modeling were :
1) related to trump and potus(Obama)
2) related to russia
3) related to media 


In [4]:
len(network.retweet_screen_name.unique())

20923

In [5]:
network.shape

(398180, 36)

In [6]:
topic0=network.loc[network['Topic'] == 0]
print("topic0.shape",topic0.shape)

topic1 =network.loc[network['Topic'] == 1]
print("topic1.shape",topic1.shape)

topic2 =network.loc[network['Topic'] == 2]
print("topic2.shape",topic2.shape)

topic0.shape (179482, 36)
topic1.shape (113336, 36)
topic2.shape (105362, 36)


In [7]:
NetworkDatasettopic0 = topic0.loc[:,['retweet_id', 'retweet_screen_name', 'user_screen_name']][:105362]

NetworkDatasettopic1 = topic1.loc[:,['retweet_id', 'retweet_screen_name', 'user_screen_name']][:105362]

NetworkDatasettopic2 = topic2.loc[:,['retweet_id', 'retweet_screen_name', 'user_screen_name']][:105362]




C:\Users\yasmi\Anaconda3\lib\site-packages\pandas\core\indexing.py:1494: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


In [8]:
%matplotlib inline
import matplotlib.pyplot as plt

from igraph import *

def plotGraph(G,filename):
    G.es["color"], G.vs["color"], G.vs["label"] = "#B3CDE3", "#FBB4AE", ""
    N=G.vcount()
    visual_style = dict()
    visual_style["bbox"] = (3000, 3000)
    visual_style["margin"] = 11
    visual_style["edge_curved"] = False
    visual_style["layout"] = G.layout("kk") 
    return plot(G,filename,**visual_style)

In [9]:
def constGraph(NetworkDatasettopic):
    i=0
    rowS, cols= NetworkDatasettopic.shape
    print(NetworkDatasettopic.head())
    topicGraph = Graph(directed=True)
    screen_name_Set=set()
    set_edge_list = set()
    print(NetworkDatasettopic.shape)
    for row in range(rowS):
        i+=1
        retweetname= str(NetworkDatasettopic.iloc[row]['retweet_screen_name'])
        Username= str(NetworkDatasettopic.iloc[row]['user_screen_name'])
        

        if retweetname not in screen_name_Set and retweetname != 'nan':
            topicGraph.add_vertex(retweetname)
            screen_name_Set.add(retweetname)
            

        if Username not in screen_name_Set:
            topicGraph.add_vertex(Username)
            screen_name_Set.add(Username)

        if retweetname !='nan':
            if retweetname != Username :
                tupl= (topicGraph.vs.find(retweetname),topicGraph.vs.find(Username))
                set_edge_list.add(tupl)
            
    set_edge_list =  list(set_edge_list)
    
    topicGraph.add_edges(set_edge_list)
    topicGraph.vs.select(_degree=0).delete()
    return topicGraph 
    

constGraph function constructs the graph for a given dataset. the graph is directed (original tweerter, who retweeted this tweet). The filters done on the graph were as follow, first we removed the nodes with degree=0, secondly the nodes who retweet a tweet they created (node pointing back to itself), lastly if the original tweerter was unknown we dont include this record in the graph.

In [10]:
def greedy(k,G):
    outdegree = G.outdegree()
    outdegree = list(set(outdegree))
    outdegree.sort(reverse=True)
    vsSet = list()
    i = 0
    while i < len(outdegree):
        GOUTdegree = G.vs.select(_outdegree = outdegree[i])["name"]
    #     print("degree",outdegree[i])
    #     print("len", topic0GraphOUTdegree)
        vsSet.extend(GOUTdegree)
        i+=1
        if len(vsSet) >= k:
            break

    return indicies(vsSet,G)

def indicies(vsSet,G):
    listkk=[]
    i=0
    while i< len(vsSet):
        xx = G.vs.find(vsSet[i])
    #     print(xx.index)
        listkk.append(xx.index)
        i+=1
    return listkk

greedy function, chooses the first k nodes with the highest outdegree. The choice of outdegree is based on the direction of the edges between the individulas. As we are interested to identify the influencers in a certain netwrok, therefore the influencers are represnted as those with highest out degree.   

In [25]:
# Import packages
%matplotlib inline
import matplotlib.pyplot as plt
from random import uniform, seed
import numpy as np
import time
from igraph import *

def propagate_ig(g,p,new_active):
    
    targets = []
    for node in new_active:
        targets += g.neighbors(node,mode="out")
        
    return(targets)

def IC(g,S,p,mc):
    """
    Input:  graph object, set of seed nodes, propagation probability
            and the number of Monte-Carlo simulations
    Output: average number of nodes influenced by the seed nodes
    """
    
    # Loop over the Monte-Carlo Simulations
    spread = []
    for i in range(mc):
        
        # Simulate propagation process      
        new_active, A = S[:], S[:]
        while new_active:

            # For each newly active node, find its neighbors that become activated
            new_ones = []
            for node in new_active:
                
                # Determine those neighbors that become infected
                np.random.seed(i)
                success = np.random.uniform(0,1,len(g.neighbors(node,mode="out"))) < p
                new_ones += list(np.extract(success, g.neighbors(node,mode="out")))

            new_active = list(set(new_ones) - set(A))
            
            # Add newly activated nodes to the set of activated nodes
            A += new_active
            
        spread.append(len(A))
        
    return(np.mean(spread))

def ICA(G,S,p,mc):
    """
    Inputs: G:  network representations 
            S:  List of seed nodes
            p:  Disease propagation probability
            mc: Number of Monte-Carlo simulations,
    Output: Average number of nodes influenced by seed nodes in S
    """
    
    # Loop over the Monte-Carlo Simulations
    spread = []
    progress = []
    for i in range(mc):
        
        # Simulate propagation process      
        new_active, A = S[:], S[:]
        while new_active:
                       
            # 1. Find out-neighbors for each newly active node
            targets = propagate_ig(G,p,new_active)
    
            # 2. Determine newly activated neighbors (set seed and sort for consistency)
            np.random.seed(i)
            success = np.random.uniform(0,1,len(targets)) < p
            new_ones = list(np.extract(success, sorted(targets)))
            
            # 3. Find newly activated nodes and add to the set of activated nodes
            new_active = list(set(new_ones) - set(A))
            A += new_active
            progress = progress + [A]
            
        spread.append(len(A))
        meanSpread = sum(spread)/len(spread)
    
    return(np.mean(spread))

def celf(g,k,p,mc):  
    """
    Input:  graph object, number of seed nodes
    Output: optimal seed set, resulting spread, time for each iteration
    """
      
    # --------------------
    # Find the first node with greedy algorithm
    # --------------------
    
    # Calculate the first iteration sorted list
    start_time = time.time() 
    marg_gain = [IC(g,[node],p,mc) for node in range(g.vcount())]

    # Create the sorted list of nodes and their marginal gain 
    Q = sorted(zip(range(g.vcount()),marg_gain), key=lambda x: x[1],reverse=True)

    # Select the first node and remove from candidate list
    S, spread, SPREAD = [Q[0][0]], Q[0][1], [Q[0][1]]
    Q, LOOKUPS, timelapse = Q[1:], [g.vcount()], [time.time()-start_time]
    
    # --------------------
    # Find the next k-1 nodes using the list-sorting procedure
    # --------------------
    
    for _ in range(k-1):    

        check, node_lookup = False, 0
        
        while not check:
            
            # Count the number of times the spread is computed
            node_lookup += 1
            
            # Recalculate spread of top node
            current = Q[0][0]
            
            # Evaluate the spread function and store the marginal gain in the list
            Q[0] = (current,IC(g,S+[current],p,mc) - spread)

            # Re-sort the list
            Q = sorted(Q, key = lambda x: x[1], reverse = True)

            # Check if previous top node stayed on top after the sort
            check = (Q[0][0] == current)

        # Select the next node
        spread += Q[0][1]
        S.append(Q[0][0])
        SPREAD.append(spread)
        LOOKUPS.append(node_lookup)
        timelapse.append(time.time() - start_time)

        # Remove the selected node from the list
        Q = Q[1:]

    return(S,SPREAD,timelapse,LOOKUPS)

In [26]:
def greedyHat(g,k,p,mc):
    """
    Input:  graph object, number of seed nodes
    Output: optimal seed set, resulting spread, time for each iteration
    """

    S, spread, timelapse, start_time = [], [], [], time.time()
    
    # Find k nodes with largest marginal gain
    for _ in range(k):

        # Loop over nodes that are not yet in seed set to find biggest marginal gain
        best_spread = 0
        for j in set(range(g.vcount()))-set(S):

            # Get the spread
            s = IC(g,S + [j],p,mc)

            # Update the winning node and spread so far
            if s > best_spread:
                best_spread, node = s, j

        # Add the selected node to the seed set
        S.append(node)
        
        # Add estimated spread and elapsed time
        spread.append(best_spread)
        timelapse.append(time.time() - start_time)

    return(S,spread,timelapse)

propagate_ig function adds the neighbours of a certain node to the set of individulas who are influenced with the rumor propagation. IC function is the algorithm of independent cascade model which takes an input of the set of active nodes and probability which indicated if the node neigbour will be influenced. at each time step IC calls propagate_ig and terminates when all the set of actived nodes influence their neigbours, return the set of influenced users. While celf chooses the K highest node with outdegree, Celf discard previous friends which were previously influenced by another node in the seed set. 

In [150]:
topic0Graph = constGraph(NetworkDatasettopic0)

#stringName="NetworkDatasettopic0.png"        
#plotGraph(topic0Graph,stringName)

   retweet_id retweet_screen_name user_screen_name
1         NaN                 NaN          Miaa925
2         NaN                 NaN        blackismy
3         NaN     rosangela_bolze       vandacapri
5         NaN                 NaN     LiberatedCit
6         NaN             svagdis   ronbauerkemper
(105362, 3)


Unexpected results occured when we called nodes resulted from greedy that we implemented as described in the lecture in which we choose the top k nodes with the highest out-degree, in comaprison to the clef algorithm. The greedy lecture implementation is faster as it chooses the highest out-degree while the other greedy implentation (https://hautahi.com/im_greedycelf
) measures spread using IC of propagation at each node and selects the k nodes with resulted in maximum spreading. Lastly CELF also depends on calling the IC at each node but CELF exclude the intesection of connected nodes between a choosen influencer and the subsequent nodes.    

In [151]:
outcelf = celf(topic0Graph ,10,0.3,3)
print(outcelf[0])

[9, 7674, 2999, 7, 18867, 11, 4983, 35057, 26162, 33174]


Regarding topic 0, the output of clef is diffrent from the greed for the highest 10 nodes, as clef seed set chooses nodes which are considered  more influencing. 

In [152]:
outIC = IC(topic0Graph , outcelf[0] , 0.7 , 100)
print(outIC)

9271.13


In [153]:
outGreedy= greedy(10,topic0Graph)
outGreedyIC=IC(topic0Graph,outGreedy,0.7,100)
print(outGreedyIC)

9061.66


In [154]:
outcelf = celf(topic0Graph ,15,0.5,3)
print(outcelf[0])

outIC = IC(topic0Graph , outcelf[0] , 0.7 , 100)
print(outIC)

[9, 7674, 11, 19227, 33, 2999, 4119, 820, 35057, 17682, 26162, 854, 293, 9643, 6550]
9932.24


In [155]:
outGreedy= greedy(15 , topic0Graph)
print(outGreedy)

outGreedyIC=IC(topic0Graph,outGreedy,0.7,100)
print(outGreedyIC)

[7674, 9, 2999, 7, 11, 35057, 18867, 4983, 12, 100, 26162, 38662, 33, 33174, 14461]
10647.93


In [156]:
topic1Graph = constGraph(NetworkDatasettopic1)

#stringName="NetworkDatasettopic17000.png"        
#plotGraph(topic1Graph,stringName)


    retweet_id retweet_screen_name user_screen_name
0          NaN     AvgAmericanDude       rudesapien
13         NaN                 NaN     CanningCooke
19         NaN           timreid69  leclerckkonenn7
23         NaN          mark_lynas    AnneGlover_EU
28         NaN     MonsieurAmerica  Hoosier_Patriot
(105362, 3)


In [157]:
outcelf = celf(topic1Graph ,15,0.5,3)
print(outcelf[0])

outIC = IC(topic1Graph , outcelf[0] , 0.7 , 100)
print(outIC)

[26979, 1261, 117, 25979, 1636, 37, 2452, 1767, 26185, 23564, 14383, 47016, 47761, 47117, 44790]
13032.03


In [158]:
outGreedy= greedy(15 , topic1Graph)
print(outGreedy)

outGreedyIC=IC(topic1Graph,outGreedy,0.7,100)
print(outGreedyIC)

[159, 1261, 117, 17, 46465, 26979, 1367, 33751, 2618, 23342, 1703, 204, 250, 31946, 2063]
17940.11


In [159]:
outcelf = celf(topic1Graph ,10,0.5,3)
print(outcelf[0])

outIC = IC(topic1Graph , outcelf[0] , 0.7 , 100)
print(outIC)

[26979, 1261, 117, 25979, 1636, 37, 2452, 1767, 26185, 23564]
12799.71


In [160]:
outGreedy= greedy(10 , topic1Graph)
print(outGreedy)

outGreedyIC=IC(topic1Graph,outGreedy,0.7,100)
print(outGreedyIC)

[159, 1261, 117, 17, 46465, 26979, 1367, 33751, 2618, 23342]
16769.31


In [12]:
topic2Graph = constGraph(NetworkDatasettopic2)

#stringName="NetworkDatasettopic25000.png"        
#plotGraph(topic2Graph,stringName)

    retweet_id retweet_screen_name user_screen_name
4          NaN                 NaN     whiskie_djim
15         NaN      John_KissMyBot    geekiestwoman
20         NaN                 NaN          sze9000
26         NaN                 NaN          sze9000
29         NaN                 NaN          rskin11
(105362, 3)


In [162]:
outcelf = celf(topic2Graph ,15,0.5,3)
print(outcelf[0])

outIC = IC(topic2Graph , outcelf[0] , 0.7 , 100)
print(outIC)

[8372, 22903, 42365, 17615, 35130, 28635, 22500, 46170, 48357, 49699, 39384, 42242, 51008, 13951, 45718]
12544.41


In [163]:
outGreedy= greedy(15 , topic2Graph)
print(outGreedy)

outGreedyIC=IC(topic2Graph,outGreedy,0.7,100)
print(outGreedyIC)

[22903, 4185, 1181, 34442, 9, 13540, 23592, 887, 2543, 42365, 17615, 6400, 9026, 1082, 35130]
16046.1


In [18]:
outcelf = celf(topic2Graph ,10,0.5,3)
print(outcelf[0])

outIC = IC(topic2Graph , outcelf[0] , 0.7 , 100)
print(outIC)

[8372, 22903, 42365, 17615, 35130, 28635, 22500, 46170, 48357, 49699]
12425.78


In [165]:
outGreedy= greedy(10 , topic2Graph)
print(outGreedy)

outGreedyIC=IC(topic2Graph,outGreedy,0.7,100)
print(outGreedyIC)

[22903, 4185, 1181, 34442, 9, 13540, 23592, 887, 2543, 42365]
14528.21


In [27]:
outGreedy= greedyHat(topic2Graph, 2 , 0.5, 1)
print(outGreedy)

#outGreedyIC=IC(topic2Graph,outGreedy[0],0.7,100)
#print(outGreedyIC)

([23592, 22903], [3521.0, 5776.0], [2.8334250450134277, 3509.9790239334106])


In [166]:
topic0Graphavgpathlength = topic0Graph.average_path_length(directed=True,unconn=True)
print(topic0Graphavgpathlength)

topic1Graphavgpathlength = topic1Graph.average_path_length(directed=True,unconn=True)
print(topic1Graphavgpathlength)

topic2Graphavgpathlength = topic2Graph.average_path_length(directed=True,unconn=True)
print(topic2Graphavgpathlength)

2.640476873620293
3.621723902999851
4.639633266658768


In [176]:

print(topic0Graph.transitivity_undirected())
print(topic1Graph.transitivity_undirected())
print(topic2Graph.transitivity_undirected())





0.000388475069047428
0.00043759731570672104
0.0003216100965979869


In [183]:

def printStats(G):
    print('Global Clustering Coefficient',Graph.transitivity_undirected(G))
    print('Average path length', Graph.average_path_length(G))
    print(G.degree_distribution(bin_width=2))

In [184]:
printStats(topic0Graph)

Global Clustering Coefficient 0.000388475069047428
Average path length 2.640476873620293
N = 42520, mean +- sd: 2.3139 +- 25.6713
Each * represents 588 items
[   0,    2): ******************************************************** (32934)
[   2,    4): *********** (6922)
[   4,    6): ** (1340)
[   6,    8):  (438)
[   8,   10):  (239)
[  10,   12):  (131)
[  12,   14):  (95)
[  14,   16):  (57)
[  16,   18):  (43)
[  18,   20):  (27)
[  20,   22):  (22)
[  22,   24):  (22)
[  24,   26):  (23)
[  26,   28):  (15)
[  28,   30):  (16)
[  30,   32):  (15)
[  32,   34):  (5)
[  34,   36):  (6)
[  36,   38):  (9)
[  38,   40):  (3)
[  40,   42):  (8)
[  42,   44):  (9)
[  44,   46):  (3)
[  46,   48):  (12)
[  48,   50):  (5)
[  50,   52):  (4)
[  52,   54):  (1)
[  54,   56):  (5)
[  56,   58):  (3)
[  58,   60):  (2)
[  60,   62):  (4)
[  62,   64):  (2)
[  64,   66):  (6)
[  66,   68):  (1)
[  68,   70):  (2)
[  70,   72):  (2)
[  72,   74):  (2)
[  74,   76):  (3)
[  76,   78):  (1)
[  78

In [180]:
printStats(topic1Graph)

Global Clustering Coefficient 0.00043759731570672104
Average path length 3.621723902999851
N = 50374, mean +- sd: 2.5899 +- 36.1826
Each * represents 690 items
[   1,    2): ******************************************************** (38668)
[   2,    3): ******** (5925)
[   3,    4): *** (2288)
[   4,    5): * (1121)
[   5,    6):  (630)
[   6,    7):  (404)
[   7,    8):  (276)
[   8,    9):  (180)
[   9,   10):  (118)
[  10,   11):  (80)
[  11,   12):  (76)
[  12,   13):  (60)
[  13,   14):  (30)
[  14,   15):  (41)
[  15,   16):  (31)
[  16,   17):  (27)
[  17,   18):  (21)
[  18,   19):  (19)
[  19,   20):  (18)
[  20,   21):  (14)
[  21,   22):  (10)
[  22,   23):  (7)
[  23,   24):  (17)
[  24,   25):  (8)
[  25,   26):  (16)
[  26,   27):  (11)
[  27,   28):  (9)
[  28,   29):  (8)
[  29,   30):  (8)
[  30,   31):  (6)
[  31,   32):  (9)
[  32,   33):  (3)
[  33,   34):  (5)
[  34,   35):  (6)
[  35,   36):  (4)
[  36,   37):  (10)
[  37,   38):  (5)
[  38,   39):  (3)
[  39,   40

In [181]:
printStats(topic2Graph)

Global Clustering Coefficient 0.0003216100965979869
Average path length 4.639633266658768
N = 51816, mean +- sd: 2.5077 +- 33.6673
Each * represents 716 items
[   1,    2): ******************************************************** (40126)
[   2,    3): ******** (5998)
[   3,    4): *** (2210)
[   4,    5): * (1089)
[   5,    6):  (615)
[   6,    7):  (386)
[   7,    8):  (260)
[   8,    9):  (165)
[   9,   10):  (125)
[  10,   11):  (84)
[  11,   12):  (82)
[  12,   13):  (62)
[  13,   14):  (55)
[  14,   15):  (41)
[  15,   16):  (29)
[  16,   17):  (27)
[  17,   18):  (32)
[  18,   19):  (33)
[  19,   20):  (23)
[  20,   21):  (21)
[  21,   22):  (8)
[  22,   23):  (8)
[  23,   24):  (19)
[  24,   25):  (19)
[  25,   26):  (8)
[  26,   27):  (11)
[  27,   28):  (6)
[  28,   29):  (4)
[  29,   30):  (7)
[  30,   31):  (5)
[  31,   32):  (9)
[  32,   33):  (6)
[  33,   34):  (5)
[  34,   35):  (4)
[  35,   36):  (4)
[  36,   37):  (7)
[  37,   38):  (5)
[  38,   39):  (5)
[  39,   40): 

In [182]:
topic0Graph.summary()

'IGRAPH DN-- 42520 49194 -- \n+ attr: name (v)'

In [185]:
stringName="NetworkDatasettopic05362.png" 
NetworkDatasettopic05362 = topic0.loc[:,['retweet_id', 'retweet_screen_name', 'user_screen_name']][:5362]
topic0Graph5362=constGraph(NetworkDatasettopic05362)
plotGraph(topic0Graph5362,stringName)

C:\Users\yasmi\Anaconda3\lib\site-packages\pandas\core\indexing.py:1494: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


   retweet_id retweet_screen_name user_screen_name
1         NaN                 NaN          Miaa925
2         NaN                 NaN        blackismy
3         NaN     rosangela_bolze       vandacapri
5         NaN                 NaN     LiberatedCit
6         NaN             svagdis   ronbauerkemper
(5362, 3)


In [186]:
stringName="NetworkDatasettopic1-5362.png" 
NetworkDatasettopic15362 = topic1.loc[:,['retweet_id', 'retweet_screen_name', 'user_screen_name']][:5362]
topic0Graph5362=constGraph(NetworkDatasettopic15362)
plotGraph(topic0Graph5362,stringName)

    retweet_id retweet_screen_name user_screen_name
0          NaN     AvgAmericanDude       rudesapien
13         NaN                 NaN     CanningCooke
19         NaN           timreid69  leclerckkonenn7
23         NaN          mark_lynas    AnneGlover_EU
28         NaN     MonsieurAmerica  Hoosier_Patriot
(5362, 3)


In [187]:
stringName="NetworkDatasettopic2-5362.png" 
NetworkDatasettopic25362 = topic2.loc[:,['retweet_id', 'retweet_screen_name', 'user_screen_name']][:5362]
topic0Graph5362=constGraph(NetworkDatasettopic25362)
plotGraph(topic0Graph5362,stringName)

    retweet_id retweet_screen_name user_screen_name
4          NaN                 NaN     whiskie_djim
15         NaN      John_KissMyBot    geekiestwoman
20         NaN                 NaN          sze9000
26         NaN                 NaN          sze9000
29         NaN                 NaN          rskin11
(5362, 3)
